In [0]:
# Import necessary PySpark functions
from pyspark.sql import SparkSession
from pyspark.sql.functions import col, abs

# Initialize Spark Session
spark = SparkSession.builder.appName("FinancialAnalyticsProject").getOrCreate()

# Load the data directly from the Databricks table you created.
# The format is "catalog.schema.tableName"
table_name = "workspace.default.bank_personal_loan_modelling"
df = spark.table(table_name)

# ----- Initial Data Exploration & Cleaning -----

# 1. Clean up column names with spaces for easier use later.
# This is a crucial step to prevent errors in subsequent cells.
df = df.withColumnRenamed("ZIP Code", "ZipCode") \
       .withColumnRenamed("Personal Loan", "PersonalLoan") \
       .withColumnRenamed("Securities Account", "SecuritiesAccount") \
       .withColumnRenamed("CD Account", "CDAccount") \
       .withColumnRenamed("CreditCard", "CreditCard")

# 2. Data Cleaning: The 'Experience' column has negative values, which are errors.
# We will replace them with their absolute values.
df = df.withColumn('Experience', abs(col('Experience')))

# --- Verification ---
# Let's verify that the data is loaded and cleaned correctly.

# Print the schema to understand data types
print("Dataset Schema:")
df.printSchema()

# Show the first 5 rows of the cleaned data
print("\nTop 5 rows of the cleaned dataset:")
df.show(5)

# Get a final count of records
print(f"\nTotal number of records in the dataset: {df.count()}")

Dataset Schema:
root
 |-- ID: long (nullable = true)
 |-- Age: long (nullable = true)
 |-- Experience: long (nullable = true)
 |-- Income: long (nullable = true)
 |-- ZipCode: long (nullable = true)
 |-- Family: long (nullable = true)
 |-- CCAvg: double (nullable = true)
 |-- Education: long (nullable = true)
 |-- Mortgage: long (nullable = true)
 |-- PersonalLoan: long (nullable = true)
 |-- SecuritiesAccount: long (nullable = true)
 |-- CDAccount: long (nullable = true)
 |-- Online: long (nullable = true)
 |-- CreditCard: long (nullable = true)


Top 5 rows of the cleaned dataset:
+---+---+----------+------+-------+------+-----+---------+--------+------------+-----------------+---------+------+----------+
| ID|Age|Experience|Income|ZipCode|Family|CCAvg|Education|Mortgage|PersonalLoan|SecuritiesAccount|CDAccount|Online|CreditCard|
+---+---+----------+------+-------+------+-----+---------+--------+------------+-----------------+---------+------+----------+
|  1| 25|         1|    49|  

In [0]:
# ==============================================================================
# CASE 1 - MBS PRICE PREDICTION (LINEAR REGRESSION)
# ==============================================================================

from pyspark.ml.feature import VectorAssembler
from pyspark.ml.regression import LinearRegression
from pyspark.ml.evaluation import RegressionEvaluator

# --- Feature Engineering ---
# We will use these columns to predict the 'Mortgage' value.
feature_cols = ['Age', 'Experience', 'Income', 'Family', 'CCAvg', 'Education', 'SecuritiesAccount', 'CDAccount', 'Online', 'CreditCard']

# VectorAssembler is a tool that combines a list of columns into a single vector column.
# Spark's ML models require features to be in this format.
assembler = VectorAssembler(inputCols=feature_cols, outputCol="features")
model_df = assembler.transform(df)

# --- Model Training ---
# Split the data into a training set (80%) and a testing set (20%).
train_data, test_data = model_df.randomSplit([0.8, 0.2], seed=1234)

# Initialize the Linear Regression model.
# We tell it our features are in the "features" column and the value we want to predict (label) is "Mortgage".
lr = LinearRegression(featuresCol="features", labelCol="Mortgage")

# Train the model using our training data.
lr_model = lr.fit(train_data)

# --- Predictions and Evaluation ---
# Make predictions on the unseen test data.
predictions = lr_model.transform(test_data)

print("MBS Price Predictions (Mortgage Value):")
predictions.select("Mortgage", "prediction").show(5)

# Evaluate the model's performance.
# RMSE (Root Mean Squared Error) tells us, on average, how far our predictions are from the actual values.
evaluator_rmse = RegressionEvaluator(labelCol="Mortgage", predictionCol="prediction", metricName="rmse")
rmse = evaluator_rmse.evaluate(predictions)
print(f"\nRoot Mean Squared Error (RMSE) on test data = {rmse:.2f}")

# R-squared (R2) tells us what percentage of the variance in the target variable is explained by our model.
evaluator_r2 = RegressionEvaluator(labelCol="Mortgage", predictionCol="prediction", metricName="r2")
r2 = evaluator_r2.evaluate(predictions)
print(f"R-squared (R2) on test data = {r2:.2f}")

MBS Price Predictions (Mortgage Value):
+--------+------------------+
|Mortgage|        prediction|
+--------+------------------+
|       0|32.912844788662845|
|       0|  44.7176296379199|
|       0| 55.51392305484531|
|     159| 86.07225794647417|
|      97| 39.72293215736021|
+--------+------------------+
only showing top 5 rows

Root Mean Squared Error (RMSE) on test data = 101.32
R-squared (R2) on test data = 0.05


In [0]:
# ==============================================================================
# CELL FOR CASE 1 VISUALIZATIONS (Dashboard-Ready)
# ==============================================================================

from pyspark.sql.functions import col

# 1. Select the columns needed for visualization from your 'predictions' DataFrame.
# The 'predictions' DataFrame was created when you ran the Case 1 code.
results_df = predictions.select(
    col("Mortgage").alias("Actual_Mortgage"), 
    col("prediction").alias("Predicted_Mortgage")
)

# 2. Calculate the 'Residuals' (the error in each prediction).
# Residual = Actual Value - Predicted Value
results_df_with_residuals = results_df.withColumn(
    "Residuals", 
    col("Actual_Mortgage") - col("Predicted_Mortgage")
)

# 3. Use the display() command. This is the key step.
# This will generate an interactive table that you can use to build visualizations.
display(results_df_with_residuals)

Actual_Mortgage Predicted_Mortgage Residuals 0 32.912844788662845 -32.912844788662845 0 44.7176296379199 -44.7176296379199 0 55.51392305484531 -55.51392305484531 159 86.07225794647417 72.92774205352583 97 39.72293215736021 57.27706784263979 0 68.54004892151394 -68.54004892151394 0 88.97734436625856 -88.97734436625856 0 72.71946021094475 -72.71946021094475 0 46.28473283326652 -46.28473283326652 211 129.4041263154799 81.59587368452009 207 62.39481931254876 144.60518068745125 0 58.90736372635795 -58.90736372635795 0 88.44067082811205 -88.44067082811205 0 75.59142103607189 -75.59142103607189 0 43.00532293910037 -43.00532293910037 336 76.58049140536113 259.41950859463884 0 57.971302973054996 -57.971302973054996 0 70.57272071711601 -70.57272071711601 0 35.5603872672104 -35.5603872672104 0 27.118223921761288 -27.118223921761288 126 45.127911631701764 80.87208836829824 0 68.80030762435251 -68.80030762435251 0 70.64143175503806 -70.64143175503806 0 36.36439917127261 -36.36439917127261 0 85.29718221922742 -85.29718221922742 0 58.290182420094425 -58.290182420094425 198 40.91758499425051 157.08241500574948 166 36.33868498900205 129.66131501099795 0 27.730182771322593 -27.730182771322593 0 42.59254252084041 -42.59254252084041 103 68.00079593562775 34.99920406437225 0 41.95505072863532 -41.95505072863532 0 52.51700363036596 -52.51700363036596 101 71.47550930433856 29.52449069566144 251 56.505279878350734 194.49472012164927 0 53.34398937399417 -53.34398937399417 0 51.65013056530921 -51.65013056530921 0 26.510317447938604 -26.510317447938604 0 52.04421872383931 -52.04421872383931 0 32.00936116673984 -32.00936116673984 0 49.877584096019525 -49.877584096019525 0 80.8968673072222 -80.8968673072222 0 60.118263085307746 -60.118263085307746 0 32.420045647378394 -32.420045647378394 0 70.99233371753724 -70.99233371753724 0 32.287334335812346 -32.287334335812346 0 31.49196573172525 -31.49196573172525 164 38.237644426367126 125.76235557363287 0 79.01677310431634 -79.01677310431634 0 78.02277076659196 -78.02277076659196 0 87.8125358264713 -87.8125358264713 89 31.584405666010447 57.41559433398955 90 43.025204565313146 46.974795434686854 0 23.167057810302012 -23.167057810302012 0 24.014682949839752 -24.014682949839752 0 48.69946315899108 -48.69946315899108 0 56.756359312722196 -56.756359312722196 209 59.02646860589951 149.9735313941005 0 59.999858626632395 -59.999858626632395 0 50.13742909167656 -50.13742909167656 99 119.37068948533944 -20.37068948533944 117 40.03062907408407 76.96937092591594 0 40.72595207600958 -40.72595207600958 77 50.03457922432652 26.96542077567348 0 61.591098932085934 -61.591098932085934 0 54.4434705565367 -54.4434705565367 0 36.837888504938455 -36.837888504938455 0 43.031659042362726 -43.031659042362726 164 50.571293734778024 113.42870626522198 0 48.04453918097965 -48.04453918097965 0 50.606022271190994 -50.606022271190994 0 40.234775681483356 -40.234775681483356 0 32.84333615774485 -32.84333615774485 0 66.84154080949912 -66.84154080949912 0 92.05657847550054 -92.05657847550054 78 18.52400924900792 59.47599075099208 419 105.93705911383987 313.06294088616016 0 39.23860600363338 -39.23860600363338 220 65.1427702261756 154.8572297738244 0 59.112575901844075 -59.112575901844075 0 45.52840924235671 -45.52840924235671 0 42.108624454352764 -42.108624454352764 0 74.19306479625358 -74.19306479625358 0 47.700181654174045 -47.700181654174045 0 44.892415085947334 -44.892415085947334 109 45.1982947197493 63.8017052802507 0 97.89440911488248 -97.89440911488248 112 35.733664052254426 76.26633594774557 133 82.42265355776954 50.577346442230464 0 43.66784869631637 -43.66784869631637 0 37.11305386823599 -37.11305386823599 124 44.846025305924485 79.15397469407552 0 44.36537801169903 -44.36537801169903 0 36.732713644820315 -36.732713644820315 0 99.62593752847118 -99.62593752847118 0 49.23958825397334 -49.23958825397334 0 39.89493371707157 -39.89493371707157 116 37.31254896789556 78.68745103210443 224 59.57119318558636 164.42880681441363 0 38.6703316087

Databricks visualization. Run in Databricks to view.

Databricks visualization. Run in Databricks to view.

In [0]:
# ==============================================================================
# CASE 2: RISK ASSESSMENT (LOGISTIC REGRESSION)
# ==============================================================================

from pyspark.ml.feature import VectorAssembler
from pyspark.ml.classification import LogisticRegression
from pyspark.ml.evaluation import BinaryClassificationEvaluator, MulticlassClassificationEvaluator

# --- Feature Engineering ---
# We will use these features to predict if a customer will accept a personal loan.
# The 'df' DataFrame is already loaded and cleaned from the very first cell.
feature_cols = ['Age', 'Experience', 'Income', 'Family', 'CCAvg', 'Education', 'Mortgage', 'SecuritiesAccount', 'CDAccount', 'Online', 'CreditCard']

assembler = VectorAssembler(inputCols=feature_cols, outputCol="features")
risk_df = assembler.transform(df)

# --- Model Training ---
# Split data into training and testing sets.
train_data, test_data = risk_df.randomSplit([0.8, 0.2], seed=1234)

# Initialize the Logistic Regression model.
# The label we want to predict is 'PersonalLoan'.
log_reg = LogisticRegression(featuresCol="features", labelCol="PersonalLoan")

# Train the model. This is where the model learns the patterns.
log_reg_model = log_reg.fit(train_data)

# --- Predictions and Evaluation ---
# Make predictions on the test data that the model has never seen before.
# This DataFrame will be used for visualizations in the next step.
predictions_case2 = log_reg_model.transform(test_data)

print("Risk Assessment Predictions (Personal Loan Acceptance):")
# We select the actual label, the model's prediction, and the probability score.
predictions_case2.select("PersonalLoan", "prediction", "probability").show(10, truncate=False)

# Evaluate model performance.
# Accuracy tells us the overall percentage of correct predictions.
evaluator_acc = MulticlassClassificationEvaluator(labelCol="PersonalLoan", predictionCol="prediction", metricName="accuracy")
accuracy = evaluator_acc.evaluate(predictions_case2)
print(f"\nModel Accuracy on test data = {accuracy*100:.2f}%")

# Area Under ROC (AUC) is a key metric for classification models.
# It measures the model's ability to distinguish between the two classes (loan vs. no loan).
# A value close to 1.0 is excellent.
evaluator_auc = BinaryClassificationEvaluator(labelCol="PersonalLoan", rawPredictionCol="rawPrediction", metricName="areaUnderROC")
auc = evaluator_auc.evaluate(predictions_case2)
print(f"Area Under ROC (AUC) on test data = {auc:.3f}")

Risk Assessment Predictions (Personal Loan Acceptance):
+------------+----------+------------------------------------------+
|PersonalLoan|prediction|probability                               |
+------------+----------+------------------------------------------+
|0           |0.0       |[0.9997815812097618,2.184187902382062E-4] |
|0           |0.0       |[0.9965148887988274,0.003485111201172564] |
|0           |0.0       |[0.9478330963808558,0.05216690361914422]  |
|0           |0.0       |[0.9160171351847677,0.08398286481523232]  |
|0           |0.0       |[0.9997980892407087,2.0191075929132385E-4]|
|0           |0.0       |[0.7072754234065305,0.2927245765934695]   |
|0           |0.0       |[0.9752947534294761,0.024705246570523864] |
|0           |0.0       |[0.9927478590321858,0.007252140967814236] |
|0           |0.0       |[0.9986873144117691,0.001312685588230944] |
|1           |1.0       |[0.001292622239460602,0.9987073777605394] |
+------------+----------+----------------------

In [0]:
# ==============================================================================
# CELL FOR CASE 2 VISUALIZATIONS (Dashboard-Ready)
# ==============================================================================

from pyspark.sql.functions import col

# 1. Select the necessary columns from the 'predictions_case2' DataFrame.
#    'PersonalLoan' is the true value.
#    'prediction' is what the model guessed.
#    'rawPrediction' is needed for the ROC curve.
classification_results_df = predictions_case2.select(
    col("PersonalLoan").cast("string"),  # Casting to string is good practice for labels
    col("prediction").cast("string"),
    col("rawPrediction")
)

# 2. Use the display() command to generate the interactive table.
display(classification_results_df)

PersonalLoan prediction rawPrediction 0 0.0 {"type":"1","size":null,"indices":null,"values":["8.428877839257629","-8.428877839257629"]} 0 0.0 {"type":"1","size":null,"indices":null,"values":["5.655764128416111","-5.655764128416111"]} 0 0.0 {"type":"1","size":null,"indices":null,"values":["2.8997301645630937","-2.8997301645630937"]} 0 0.0 {"type":"1","size":null,"indices":null,"values":["2.3894222832931433","-2.3894222832931433"]} 0 0.0 {"type":"1","size":null,"indices":null,"values":["8.507482812720097","-8.507482812720097"]} 0 0.0 {"type":"1","size":null,"indices":null,"values":["0.8821880010784877","-0.8821880010784877"]} 0 0.0 {"type":"1","size":null,"indices":null,"values":["3.6757241036808885","-3.6757241036808885"]} 0 0.0 {"type":"1","size":null,"indices":null,"values":["4.919179982228066","-4.919179982228066"]} 0 0.0 {"type":"1","size":null,"indices":null,"values":["6.63436662502302","-6.63436662502302"]} 1 1.0 {"type":"1","size":null,"indices":null,"values":["-6.649788921672503","6.649788921672503"]} 0 0.0 {"type":"1","size":null,"indices":null,"values":["6.981415253891289","-6.981415253891289"]} 0 0.0 {"type":"1","size":null,"indices":null,"values":["3.8632707715074073","-3.8632707715074073"]} 1 1.0 {"type":"1","size":null,"indices":null,"values":["-0.6036999398498928","0.6036999398498928"]} 0 0.0 {"type":"1","size":null,"indices":null,"values":["5.283095813281779","-5.283095813281779"]} 0 0.0 {"type":"1","size":null,"indices":null,"values":["6.057694905207585","-6.057694905207585"]} 0 0.0 {"type":"1","size":null,"indices":null,"values":["3.7102668192731265","-3.7102668192731265"]} 0 0.0 {"type":"1","size":null,"indices":null,"values":["3.811053578796079","-3.811053578796079"]} 0 0.0 {"type":"1","size":null,"indices":null,"values":["4.242771298334661","-4.242771298334661"]} 0 0.0 {"type":"1","size":null,"indices":null,"values":["5.327510614403128","-5.327510614403128"]} 0 0.0 {"type":"1","size":null,"indices":null,"values":["7.0804771078890845","-7.0804771078890845"]} 0 0.0 {"type":"1","size":null,"indices":null,"values":["4.473356976276094","-4.473356976276094"]} 0 0.0 {"type":"1","size":null,"indices":null,"values":["0.10900959382218645","-0.10900959382218645"]} 1 0.0 {"type":"1","size":null,"indices":null,"values":["0.45096451345101407","-0.45096451345101407"]} 0 0.0 {"type":"1","size":null,"indices":null,"values":["4.391800940866441","-4.391800940866441"]} 0 0.0 {"type":"1","size":null,"indices":null,"values":["3.925877847231334","-3.925877847231334"]} 0 0.0 {"type":"1","size":null,"indices":null,"values":["7.395912053821428","-7.395912053821428"]} 0 0.0 {"type":"1","size":null,"indices":null,"values":["4.9967887424274","-4.9967887424274"]} 0 0.0 {"type":"1","size":null,"indices":null,"values":["8.090315401638456","-8.090315401638456"]} 0 0.0 {"type":"1","size":null,"indices":null,"values":["7.654944714191469","-7.654944714191469"]} 0 0.0 {"type":"1","size":null,"indices":null,"values":["8.574302064425135","-8.574302064425135"]} 0 0.0 {"type":"1","size":null,"indices":null,"values":["4.676557364524523","-4.676557364524523"]} 0 0.0 {"type":"1","size":null,"indices":null,"values":["4.499461700191597","-4.499461700191597"]} 0 0.0 {"type":"1","size":null,"indices":null,"values":["6.055571457946373","-6.055571457946373"]} 0 0.0 {"type":"1","size":null,"indices":null,"values":["5.505926439988778","-5.505926439988778"]} 0 0.0 {"type":"1","size":null,"indices":null,"values":["4.89270048300291","-4.89270048300291"]} 0 0.0 {"type":"1","size":null,"indices":null,"values":["3.305434163944444","-3.305434163944444"]} 0 0.0 {"type":"1","size":null,"indices":null,"values":["3.858682033929373","-3.858682033929373"]} 0 0.0 {"type":"1","size":null,"indices":null,"values":["11.119133604376533","-11.119133604376533"]} 0 0.0 {"type":"1","size":null,"indices":null,"values":["6.167436388847811","-6.167436388847811"]} 0 0.0 {"type":"1","size":null,"indices":null,"values":["9.193200860450737","-9.193200860450737"]} 0 0.0 {"type":"1","size"

Databricks visualization. Run in Databricks to view.

In [0]:
# ==============================================================================
# CELL FOR CASE 3: TRADING DECISION SUPPORT (K-MEANS CLUSTERING)
# ==============================================================================

from pyspark.ml.clustering import KMeans
from pyspark.ml.feature import VectorAssembler, StandardScaler

# --- Feature Engineering ---
# We select key features that will help differentiate customer segments.
# The 'df' DataFrame is already loaded and cleaned from the very first cell.
cluster_cols = ['Income', 'CCAvg', 'Age', 'Education', 'Mortgage']

# Combine the selected features into a single vector column.
assembler = VectorAssembler(inputCols=cluster_cols, outputCol="assembled_features")
assembled_df = assembler.transform(df)

# K-Means is sensitive to the scale of data, so we must scale our features.
# StandardScaler transforms the data to have a mean of 0 and standard deviation of 1.
scaler = StandardScaler(inputCol="assembled_features", outputCol="features")
scaler_model = scaler.fit(assembled_df)
scaled_df = scaler_model.transform(assembled_df)

# --- Model Training ---
# Initialize K-Means to find 3 distinct clusters (for "Buy", "Hold", "Sell").
kmeans = KMeans(featuresCol="features", k=3, seed=1234)

# Train the clustering model.
kmeans_model = kmeans.fit(scaled_df)

# --- Assign Clusters and Analyze ---
# Add a 'prediction' column to our DataFrame, which contains the cluster ID for each customer.
# This DataFrame will be used for visualizations in the next step.
clustered_df = kmeans_model.transform(scaled_df)

print("Customers with their assigned cluster IDs:")
clustered_df.select("ID", "Income", "CCAvg", "prediction").show(10)

# --- Interpretation of Clusters ---
# To understand what each cluster represents, we calculate the average value
# of our features for each cluster. This helps us create a "persona" for each segment.
print("\nAnalysis of Cluster Centers (Average values for each feature):")
cluster_summary = clustered_df.groupBy("prediction").mean(*cluster_cols)
cluster_summary.show()

# INTERPRETATION GUIDE:
# Look at the table above. You might see:
# - A cluster with high "avg(Income)" and high "avg(CCAvg)". You could label this your "BUY" group (prime customers).
# - A cluster with very low "avg(Income)" and "avg(Mortgage)". You could label this a "SELL" or "Low Priority" group.
# - A cluster with moderate values across the board. This could be your "HOLD" or "Nurture" group.

Customers with their assigned cluster IDs:
+---+------+-----+----------+
| ID|Income|CCAvg|prediction|
+---+------+-----+----------+
|  1|    49|  1.6|         1|
|  2|    34|  1.5|         1|
|  3|    11|  1.0|         1|
|  4|   100|  2.7|         0|
|  5|    45|  1.0|         0|
|  6|    29|  0.4|         0|
|  7|    72|  1.5|         1|
|  8|    22|  0.3|         0|
|  9|    81|  0.6|         0|
| 10|   180|  8.9|         2|
+---+------+-----+----------+
only showing top 10 rows

Analysis of Cluster Centers (Average values for each feature):
+----------+------------------+------------------+------------------+------------------+------------------+
|prediction|       avg(Income)|        avg(CCAvg)|          avg(Age)|    avg(Education)|     avg(Mortgage)|
+----------+------------------+------------------+------------------+------------------+------------------+
|         1|  60.7355175688509|1.3208926875593543|48.332383665716996|1.2867996201329535|42.356125356125354|
|         0|54.5

In [0]:
# ==============================================================================
# CELL FOR CASE 3 VISUALIZATIONS (Dashboard-Ready)
# ==============================================================================

# We will use the 'clustered_df' DataFrame created in the previous cell.
# It contains all the original data plus the new 'prediction' column with the cluster ID.

# The display() command is all we need to create a dashboard-ready output.
# It will generate an interactive table from which we can build our chart.
display(clustered_df)

ID Age Experience Income ZipCode Family CCAvg Education Mortgage PersonalLoan SecuritiesAccount CDAccount Online CreditCard assembled_features features prediction 1 25 1 49 91107 4 1.6 1 0 0 1 0 0 0 {"type":"1","size":null,"indices":null,"values":["49.0","1.6","25.0","1.0","0.0"]} {"type":"1","size":null,"indices":null,"values":["1.0644368970896085","0.9155104160865433","2.1808984364135466","1.1906617598398077","0.0"]} 1 2 45 19 34 90089 3 1.5 1 0 0 1 0 0 0 {"type":"1","size":null,"indices":null,"values":["34.0","1.5","45.0","1.0","0.0"]} {"type":"1","size":null,"indices":null,"values":["0.7385888673682998","0.8582910150811343","3.925617185544384","1.1906617598398077","0.0"]} 1 3 39 15 11 94720 1 1.0 1 0 0 0 0 0 0 {"type":"1","size":null,"indices":null,"values":["11.0","1.0","39.0","1.0","0.0"]} {"type":"1","size":null,"indices":null,"values":["0.2389552217956264","0.5721940100540895","3.4022015608051333","1.1906617598398077","0.0"]} 1 4 35 9 100 94112 1 2.7 2 0 0 0 0 0 0 {"type":"1","size":null,"indices":null,"values":["100.0","2.7","35.0","2.0","0.0"]} {"type":"1","size":null,"indices":null,"values":["2.1723201981420583","1.544923827146042","3.0532578109789656","2.3813235196796154","0.0"]} 0 5 35 8 45 91330 4 1.0 2 0 0 0 0 0 1 {"type":"1","size":null,"indices":null,"values":["45.0","1.0","35.0","2.0","0.0"]} {"type":"1","size":null,"indices":null,"values":["0.9775440891639262","0.5721940100540895","3.0532578109789656","2.3813235196796154","0.0"]} 0 6 37 13 29 92121 4 0.4 2 155 0 0 0 1 0 {"type":"1","size":null,"indices":null,"values":["29.0","0.4","37.0","2.0","155.0"]} {"type":"1","size":null,"indices":null,"values":["0.6299728574611969","0.22887760402163582","3.2277296858920494","2.3813235196796154","1.5238836499730208"]} 0 7 53 27 72 91711 2 1.5 2 0 0 0 0 1 0 {"type":"1","size":null,"indices":null,"values":["72.0","1.5","53.0","2.0","0.0"]} {"type":"1","size":null,"indices":null,"values":["1.5640705426622818","0.8582910150811343","4.623504685196719","2.3813235196796154","0.0"]} 1 8 50 24 22 93943 1 0.3 3 0 0 0 0 0 1 {"type":"1","size":null,"indices":null,"values":["22.0","0.3","50.0","3.0","0.0"]} {"type":"1","size":null,"indices":null,"values":["0.4779104435912528","0.17165820301622686","4.361796872827093","3.5719852795194234","0.0"]} 0 9 35 10 81 90089 3 0.6 2 104 0 0 0 1 0 {"type":"1","size":null,"indices":null,"values":["81.0","0.6","35.0","2.0","104.0"]} {"type":"1","size":null,"indices":null,"values":["1.7595793604950671","0.3433164060324537","3.0532578109789656","2.3813235196796154","1.022476771594801"]} 0 10 34 9 180 93023 1 8.9 3 0 1 0 0 0 0 {"type":"1","size":null,"indices":null,"values":["180.0","8.9","34.0","3.0","0.0"]} {"type":"1","size":null,"indices":null,"values":["3.910176356655705","5.092526689481397","2.9660218735224237","3.5719852795194234","0.0"]} 2 11 65 39 105 94710 4 2.4 3 0 0 0 0 0 0 {"type":"1","size":null,"indices":null,"values":["105.0","2.4","65.0","3.0","0.0"]} {"type":"1","size":null,"indices":null,"values":["2.280936208049161","1.373265624129815","5.670335934675221","3.5719852795194234","0.0"]} 0 12 29 5 45 90277 3 0.1 2 0 0 0 0 1 0 {"type":"1","size":null,"indices":null,"values":["45.0","0.1","29.0","2.0","0.0"]} {"type":"1","size":null,"indices":null,"values":["0.9775440891639262","0.057219401005408954","2.5298421862397142","2.3813235196796154","0.0"]} 0 13 48 23 114 93106 2 3.8 3 0 0 1 0 0 0 {"type":"1","size":null,"indices":null,"values":["114.0","3.8","48.0","3.0","0.0"]} {"type":"1","size":null,"indices":null,"values":["2.4764450258819464","2.17433723820554","4.1873249979140095","3.5719852795194234","0.0"]} 0 14 59 32 40 94920 4 2.5 2 0 0 0 0 1 0 {"type":"1","size":null,"indices":null,"values":["40.0","2.5","59.0","2.0","0.0"]} {"type":"1","size":null,"indices":null,"values":["0.8689280792568232","1.430485025135224","5.146920309935971","2.3813235196796154","0.0"]} 1 15 67 41 112 91741 1 2.0 1 0 0 1 0 0 0 {"type":"1","size":null,"indices":null,"values":["112.0","2.0","67.0","1.0","0.0

Databricks visualization. Run in Databricks to view.

Databricks visualization. Run in Databricks to view.

In [0]:
# ==============================================================================
# CELL FOR CASE 4: INTEREST RATE IMPACT SIMULATION (Corrected for Serverless)
# ==============================================================================
# This cell uses the classification model ('log_reg_model') we trained in Case 2.

from pyspark.ml.feature import VectorAssembler
from pyspark.sql.functions import col, udf, avg
from pyspark.ml.linalg import Vector

# --- Simulation Setup ---
rate_multipliers = [1.0, 1.1, 1.25, 1.5, 1.75]
simulation_results = []

print("Starting Interest Rate Impact Simulation...")

# --- Simulation Loop ---
for multiplier in rate_multipliers:
    # 1. Create a temporary DataFrame with a simulated 'CCAvg' value.
    simulated_df = df.withColumn("CCAvg_sim", col("CCAvg") * multiplier)

    # 2. Re-assemble the features for the model.
    sim_assembler = VectorAssembler(
        inputCols=['Age', 'Experience', 'Income', 'Family', 'CCAvg_sim', 'Education', 'Mortgage', 'SecuritiesAccount', 'CDAccount', 'Online', 'CreditCard'],
        outputCol="features"
    )
    sim_featured_df = sim_assembler.transform(simulated_df)

    # 3. Use our previously trained model to make new predictions.
    sim_predictions = log_reg_model.transform(sim_featured_df)

    # 4. Helper function to extract the probability of a positive outcome (Loan = 1).
    extract_prob_udf = udf(lambda v: float(v[1]), 'float')
    
    # 5. Calculate the average probability using modern DataFrame functions.
    #    THIS IS THE CORRECTED PART.
    avg_prob_df = sim_predictions.withColumn('prob_loan', extract_prob_udf(col('probability'))) \
                                 .agg(avg("prob_loan"))
    
    # Collect the single result from the aggregation.
    avg_prob = avg_prob_df.collect()[0][0]
    
    # 6. Store the result.
    simulation_results.append({'Rate_Multiplier': multiplier, 'Avg_Loan_Acceptance_Prob': avg_prob})
    
    print(f"  -> For Rate Multiplier: {multiplier:.2f}, the Average Loan Acceptance Probability is: {avg_prob:.4f}")

print("\nSimulation complete.")

Starting Interest Rate Impact Simulation...
  -> For Rate Multiplier: 1.00, the Average Loan Acceptance Probability is: 0.0993
  -> For Rate Multiplier: 1.10, the Average Loan Acceptance Probability is: 0.1010
  -> For Rate Multiplier: 1.25, the Average Loan Acceptance Probability is: 0.1035
  -> For Rate Multiplier: 1.50, the Average Loan Acceptance Probability is: 0.1079
  -> For Rate Multiplier: 1.75, the Average Loan Acceptance Probability is: 0.1124

Simulation complete.


In [0]:
# ==============================================================================
# CELL FOR CASE 4 VISUALIZATIONS (Dashboard-Ready)
# ==============================================================================
import pandas as pd

# The 'simulation_results' list was created in the previous cell.
# We will convert it into a Spark DataFrame for use with display().
if 'simulation_results' in locals() and simulation_results:
    # Convert the list of dictionaries to a Spark DataFrame.
    results_spark_df = spark.createDataFrame(pd.DataFrame(simulation_results))
    
    # Use the display() command to generate an interactive table.
    # From this table, we will build our line chart.
    print("Simulation results ready for visualization:")
    display(results_spark_df)
else:
    print("The 'simulation_results' list is empty or was not created.")
    print("Please re-run the previous cell (Case 4 Simulation) to generate the results.")

Simulation results ready for visualization:


Rate_Multiplier Avg_Loan_Acceptance_Prob 1.0 0.09931564417045428 1.1 0.1009950802211204 1.25 0.10354974974393771 1.5 0.1078977653122808 1.75 0.1123503803647487

Databricks visualization. Run in Databricks to view.

Databricks visualization. Run in Databricks to view.

In [0]:
# ==============================================================================
# CELL FOR CASE 5: DEFAULT/PREPAYMENT ANALYSIS (DECISION TREE)
# ==============================================================================

from pyspark.ml.feature import VectorAssembler
from pyspark.ml.classification import DecisionTreeClassifier
from pyspark.ml.evaluation import MulticlassClassificationEvaluator

# --- Feature Engineering ---
# We will predict who has a CD Account based on their financial profile.
# The 'df' DataFrame is already loaded and cleaned from the very first cell.
feature_cols = ['Age', 'Experience', 'Income', 'Family', 'CCAvg', 'Education', 'Mortgage', 'PersonalLoan', 'SecuritiesAccount', 'Online', 'CreditCard']

assembler = VectorAssembler(inputCols=feature_cols, outputCol="features")
cd_account_df = assembler.transform(df)

# --- Model Training ---
train_data, test_data = cd_account_df.randomSplit([0.8, 0.2], seed=1234)

# Initialize the Decision Tree model. The label we want to predict is 'CDAccount'.
dt = DecisionTreeClassifier(featuresCol="features", labelCol="CDAccount")

# Train the model.
dt_model = dt.fit(train_data)

# --- Predictions and Evaluation ---
# Make predictions on the test data.
# This DataFrame will be used for visualizations in the next step.
predictions_case5 = dt_model.transform(test_data)

print("Predictions for CD Account Holding (Proxy for Financial Stability):")
predictions_case5.select("CDAccount", "prediction").show(10)

# Evaluate the model's accuracy.
evaluator = MulticlassClassificationEvaluator(labelCol="CDAccount", predictionCol="prediction", metricName="accuracy")
accuracy = evaluator.evaluate(predictions_case5)
print(f"\nModel Accuracy for predicting CD Account ownership = {accuracy*100:.2f}%")

# The 'toDebugString' is the most valuable part. It prints the simple "if-then" rules 
# the model learned, which are easy to interpret for identifying low-risk customers.
print("\n--- Decision Tree Rules ---")
print(dt_model.toDebugString)

Predictions for CD Account Holding (Proxy for Financial Stability):
+---------+----------+
|CDAccount|prediction|
+---------+----------+
|        0|       0.0|
|        0|       0.0|
|        0|       0.0|
|        0|       0.0|
|        0|       0.0|
|        0|       0.0|
|        0|       0.0|
|        0|       0.0|
|        0|       0.0|
|        1|       1.0|
+---------+----------+
only showing top 10 rows

Model Accuracy for predicting CD Account ownership = 97.18%

--- Decision Tree Rules ---
DecisionTreeClassificationModel: uid=DecisionTreeClassifier_4dd3134bd4df, depth=5, numNodes=21, numClasses=2, numFeatures=11
  If (feature 7 <= 0.5)
   If (feature 8 <= 0.5)
    Predict: 0.0
   Else (feature 8 > 0.5)
    If (feature 10 <= 0.5)
     Predict: 0.0
    Else (feature 10 > 0.5)
     If (feature 9 <= 0.5)
      Predict: 0.0
     Else (feature 9 > 0.5)
      Predict: 1.0
  Else (feature 7 > 0.5)
   If (feature 10 <= 0.5)
    If (feature 8 <= 0.5)
     Predict: 0.0
    Else (feature

In [0]:
# ==============================================================================
# CELL FOR CASE 5 VISUALIZATION - FEATURE IMPORTANCE (Dashboard-Ready)
# ==============================================================================

import pandas as pd

# The 'dt_model' (Decision Tree Model) and 'feature_cols' list were created
# in the previous cell when you trained the model for Case 5.

# 1. Extract the feature importance scores from the trained model.
#    The model assigns a score to each feature based on how much it helped in making correct predictions.
importances = dt_model.featureImportances.toArray()

# 2. Create a Pandas DataFrame to hold the feature names and their corresponding importance scores.
feature_importance_pd = pd.DataFrame({
    'Feature': feature_cols,
    'Importance': importances
}).sort_values(by='Importance', ascending=False) # Sorting makes the chart much clearer

# 3. Convert the Pandas DataFrame back to a Spark DataFrame.
feature_importance_df = spark.createDataFrame(feature_importance_pd)

# 4. Use the display() command. This will generate the interactive table we need to build our bar chart.
print("Feature Importances for Predicting Financial Stability (CD Account):")
display(feature_importance_df)

Feature Importances for Predicting Financial Stability (CD Account):


Feature Importance CreditCard 0.3257649688275374 Online 0.28834862188048394 SecuritiesAccount 0.2208802682627185 PersonalLoan 0.15659171173126374 Mortgage 0.008414429297996382 Age 0.0 Experience 0.0 Income 0.0 Family 0.0 CCAvg 0.0 Education 0.0

Databricks visualization. Run in Databricks to view.